## Bring end timelines and target vector

In [1]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
import pickle
import sys , numpy as np
mod = sys.modules[__name__]
seed = 0

In [2]:
# initialize
kinds = "Additional"
tier = "CHALLENGER"

# Original
#filePath = "./Refined Timeline DataFrames/{0}/{1}/{1}{2}.csv"

#Additional
filePath = "./Refined Timeline DataFrames/{0}/{1}/Train/{1}{2}.csv"

endTimes = pd.read_pickle("endtimes/{}/Train/{}endTimes.pkl".format(kinds, tier))
k = 1000
start, end = 1, 50
dataset = []

# get target vector 
df = pd.read_csv(filePath.format(kinds, tier, 20))
target = np.array(df['blue_win'])

# get game and timelines 
for idx, endTime in enumerate(endTimes):
    endTimes[idx] = (idx, endTime)

# train / test split 
endTimes_train, endTimes_test, y_train, y_test = train_test_split(endTimes, target,
                                                                    test_size = 0.2,
                                                                    random_state = seed)

In [3]:
for tl in range(start, end+1):
    df = pd.read_csv(filePath.format(kinds, tier, tl))
    del df['game_id']
    del df['blue_win']
    setattr(mod, "df_{}".format(tl), df)
eval("df_"+str(30))

total_gold  current_gold  total_level  avg_level  kills_total_minion  \
0            7478          4893            5        1.0                   9   
1           -8770         -1613           -8       -1.6                  71   
2           -7459         -3188           -5       -1.0                 -31   
3           -9446         -6906           -6       -1.2                 -35   
4            5704          1744            6        1.2                 -12   
...           ...           ...          ...        ...                 ...   
31995        4682          6341            6        1.2                 -29   
31996        4819          -788            7        1.4                  28   
31997        9354          5414            7        1.4                  38   
31998       13187          4014            8        1.6                 107   
31999       14608          5393            7        1.4                  91   

       kills_total_jungle_minion  first_blood  kills  deaths  assists  ...  \
0                             31            1     10     -10       13  ...   
1                            -79            1     -8       8      -17  ...   
2                            -36           -1    -15      15      -17  ...   
3                              7           -1    -14      14      -45  ...   
4                             48            1      6      -6       11  ...   
...                          ...          ...    ...     ...      ...  ...   
31995                        -24            1     15     -15       22  ...   
31996                        -15            1      7      -7       14  ...   
31997                         38           -1     11     -11        5  ...   
31998                         65            1     23     -23       31  ...   
31999                         33            1     18     -18       29  ...   

       kills_total_towers  kills_mid_towers  kills_top_towers  \
0                       6                 5                 1   
1                      -5                -2                -1   
2                      -4                -3                 0   
3                      -6                -2                -2   
4                       1                 1                -1   
...                   ...               ...               ...   
31995                  -5                -2                -2   
31996                  -2                 1                -1   
31997                   3                 3                 0   
31998                   3                 1                 2   
31999                   7                 3                 2   

       kills_bot_towers  kills_inhibitors  first_dragon  total_dragons  \
0                     0                 1            -1              1   
1                    -2                 0            -1             -4   
2                    -1                -1            -1             -1   
3                    -2                 0            -1             -3   
4                     1                 0            -1              1   
...                 ...               ...           ...            ...   
31995                -1                 0            -1              0   
31996                -2                 0            -1              0   
31997                 0                 1             1              2   
31998                 0                 1             1              3   
31999                 2                 1             1              2   

       rift_heralds  first_baron  total_barons  
0                 2            0             0  
1                 0           -1            -2  
2                -2            0             0  
3                 0           -1            -1  
4                 2            1             1  
...             ...          ...           ...  
31995            -1            0             0  
31996             0            1             1  
31997     

In [4]:
target

array([1, 0, 0, ..., 1, 1, 1], dtype=int64)

In [ ]:
eval("df_"+str(35)).iloc[1027]

## Make training dataset

In [5]:
print("In training data whole game size is:", len(endTimes_train))

######### initialize ########
dataPath = "./RNN Dataset/{0}/Train/Data/{0}{1}.pkl"
targetPath = "./RNN Dataset/{0}/Train/Target/{0}{1}.pkl"
store_cnt = 1
#############################

for idx in range(len(endTimes_train)):
    miniset = []
    endTime = 0
    print(" >> Processing index : {}".format(idx))
    game, endTime = endTimes_train[idx]
    
    for tl in range(start, endTime+1):
        last_timeline = tl
        miniset.append(np.array(eval("df_"+str(tl)).iloc[game]))
        
    print("miniset's size is:", np.shape(miniset))
    dataset.append(np.array(miniset))
    print(" >> >> Processing index : {0} game - {1} minutes game length data is loaded.\n".format(game, last_timeline))
    
    if (idx+1) % (10*k) == 0:
        dataset = np.array(dataset)
        
        path = dataPath.format(tier, store_cnt)
        with open(path, "wb") as f: pickle.dump(dataset, f)
            
        path = targetPath.format(tier, store_cnt)
        with open(path, "wb") as f:
            b1, b2 = (store_cnt-1)*10*k, store_cnt*10*k
            pickle.dump(y_train[b1:b2], f)
            
        dataset = []
        store_cnt += 1
        print("Intermediate storing has been done.\n")

dataset = np.array(dataset)
path = dataPath.format(tier, store_cnt)
with open(path, "wb") as f: pickle.dump(dataset, f)
    
path = targetPath.format(tier, store_cnt)
with open(path, "wb") as f:
    b1 = (store_cnt-1)*10*k
    pickle.dump(y_train[b1:], f)
    
print("\n\n\n\nFinished. Final dataset.shape:", dataset.shape)

In training data whole game size is: 25600
 >> Processing index : 0
miniset's size is: (25, 24)
 >> >> Processing index : 3549 game - 25 minutes game length data is loaded.

 >> Processing index : 1
miniset's size is: (14, 24)
 >> >> Processing index : 28460 game - 14 minutes game length data is loaded.

 >> Processing index : 2
miniset's size is: (5, 24)
 >> >> Processing index : 6225 game - 5 minutes game length data is loaded.

 >> Processing index : 3
miniset's size is: (37, 24)
 >> >> Processing index : 20232 game - 37 minutes game length data is loaded.

 >> Processing index : 4
miniset's size is: (16, 24)
 >> >> Processing index : 31372 game - 16 minutes game length data is loaded.

 >> Processing index : 5
miniset's size is: (22, 24)
 >> >> Processing index : 829 game - 22 minutes game length data is loaded.

 >> Processing index : 6
miniset's size is: (28, 24)
 >> >> Processing index : 17071 game - 28 minutes game length data is loaded.

 >> Processing index : 7
miniset's size

miniset's size is: (32, 24)
 >> >> Processing index : 10596 game - 32 minutes game length data is loaded.

 >> Processing index : 69
miniset's size is: (25, 24)
 >> >> Processing index : 4825 game - 25 minutes game length data is loaded.

 >> Processing index : 70
miniset's size is: (36, 24)
 >> >> Processing index : 5233 game - 36 minutes game length data is loaded.

 >> Processing index : 71
miniset's size is: (26, 24)
 >> >> Processing index : 26541 game - 26 minutes game length data is loaded.

 >> Processing index : 72
miniset's size is: (24, 24)
 >> >> Processing index : 3038 game - 24 minutes game length data is loaded.

 >> Processing index : 73
miniset's size is: (20, 24)
 >> >> Processing index : 129 game - 20 minutes game length data is loaded.

 >> Processing index : 74
miniset's size is: (31, 24)
 >> >> Processing index : 9259 game - 31 minutes game length data is loaded.

 >> Processing index : 75
miniset's size is: (34, 24)
 >> >> Processing index : 1894 game - 34 minute

miniset's size is: (17, 24)
 >> >> Processing index : 21496 game - 17 minutes game length data is loaded.

 >> Processing index : 133
miniset's size is: (12, 24)
 >> >> Processing index : 20337 game - 12 minutes game length data is loaded.

 >> Processing index : 134
miniset's size is: (13, 24)
 >> >> Processing index : 23236 game - 13 minutes game length data is loaded.

 >> Processing index : 135
miniset's size is: (24, 24)
 >> >> Processing index : 21905 game - 24 minutes game length data is loaded.

 >> Processing index : 136
miniset's size is: (13, 24)
 >> >> Processing index : 14589 game - 13 minutes game length data is loaded.

 >> Processing index : 137
miniset's size is: (21, 24)
 >> >> Processing index : 16065 game - 21 minutes game length data is loaded.

 >> Processing index : 138
miniset's size is: (28, 24)
 >> >> Processing index : 18803 game - 28 minutes game length data is loaded.

 >> Processing index : 139
miniset's size is: (19, 24)
 >> >> Processing index : 17851 ga

miniset's size is: (17, 24)
 >> >> Processing index : 17554 game - 17 minutes game length data is loaded.

 >> Processing index : 199
miniset's size is: (25, 24)
 >> >> Processing index : 10025 game - 25 minutes game length data is loaded.

 >> Processing index : 200
miniset's size is: (20, 24)
 >> >> Processing index : 30090 game - 20 minutes game length data is loaded.

 >> Processing index : 201
miniset's size is: (24, 24)
 >> >> Processing index : 11598 game - 24 minutes game length data is loaded.

 >> Processing index : 202
miniset's size is: (24, 24)
 >> >> Processing index : 20798 game - 24 minutes game length data is loaded.

 >> Processing index : 203
miniset's size is: (33, 24)
 >> >> Processing index : 23593 game - 33 minutes game length data is loaded.

 >> Processing index : 204
miniset's size is: (21, 24)
 >> >> Processing index : 10685 game - 21 minutes game length data is loaded.

 >> Processing index : 205
miniset's size is: (16, 24)
 >> >> Processing index : 1578 gam

miniset's size is: (23, 24)
 >> >> Processing index : 21941 game - 23 minutes game length data is loaded.

 >> Processing index : 323
miniset's size is: (13, 24)
 >> >> Processing index : 31664 game - 13 minutes game length data is loaded.

 >> Processing index : 324
miniset's size is: (31, 24)
 >> >> Processing index : 19699 game - 31 minutes game length data is loaded.

 >> Processing index : 325
miniset's size is: (36, 24)
 >> >> Processing index : 30340 game - 36 minutes game length data is loaded.

 >> Processing index : 326
miniset's size is: (27, 24)
 >> >> Processing index : 3310 game - 27 minutes game length data is loaded.

 >> Processing index : 327
miniset's size is: (22, 24)
 >> >> Processing index : 28404 game - 22 minutes game length data is loaded.

 >> Processing index : 328
miniset's size is: (31, 24)
 >> >> Processing index : 8391 game - 31 minutes game length data is loaded.

 >> Processing index : 329
miniset's size is: (13, 24)
 >> >> Processing index : 12447 game

...

miniset's size is: (22, 24)
 >> >> Processing index : 22450 game - 22 minutes game length data is loaded.

 >> Processing index : 25280
miniset's size is: (30, 24)
 >> >> Processing index : 8922 game - 30 minutes game length data is loaded.

 >> Processing index : 25281
miniset's size is: (32, 24)
 >> >> Processing index : 3886 game - 32 minutes game length data is loaded.

 >> Processing index : 25282
miniset's size is: (17, 24)
 >> >> Processing index : 24451 game - 17 minutes game length data is loaded.

 >> Processing index : 25283
miniset's size is: (23, 24)
 >> >> Processing index : 31639 game - 23 minutes game length data is loaded.

 >> Processing index : 25284
miniset's size is: (25, 24)
 >> >> Processing index : 12585 game - 25 minutes game length data is loaded.

 >> Processing index : 25285
miniset's size is: (30, 24)
 >> >> Processing index : 2121 game - 30 minutes game length data is loaded.

 >> Processing index : 25286
miniset's size is: (21, 24)
 >> >> Processing index

miniset's size is: (17, 24)
 >> >> Processing index : 18247 game - 17 minutes game length data is loaded.

 >> Processing index : 25346
miniset's size is: (21, 24)
 >> >> Processing index : 8717 game - 21 minutes game length data is loaded.

 >> Processing index : 25347
miniset's size is: (20, 24)
 >> >> Processing index : 10527 game - 20 minutes game length data is loaded.

 >> Processing index : 25348
miniset's size is: (17, 24)
 >> >> Processing index : 469 game - 17 minutes game length data is loaded.

 >> Processing index : 25349
miniset's size is: (21, 24)
 >> >> Processing index : 5446 game - 21 minutes game length data is loaded.

 >> Processing index : 25350
miniset's size is: (28, 24)
 >> >> Processing index : 22649 game - 28 minutes game length data is loaded.

 >> Processing index : 25351
miniset's size is: (24, 24)
 >> >> Processing index : 27387 game - 24 minutes game length data is loaded.

 >> Processing index : 25352
miniset's size is: (19, 24)
 >> >> Processing index 

miniset's size is: (35, 24)
 >> >> Processing index : 13683 game - 35 minutes game length data is loaded.

 >> Processing index : 25409
miniset's size is: (23, 24)
 >> >> Processing index : 13866 game - 23 minutes game length data is loaded.

 >> Processing index : 25410
miniset's size is: (26, 24)
 >> >> Processing index : 5294 game - 26 minutes game length data is loaded.

 >> Processing index : 25411
miniset's size is: (33, 24)
 >> >> Processing index : 8467 game - 33 minutes game length data is loaded.

 >> Processing index : 25412
miniset's size is: (18, 24)
 >> >> Processing index : 23334 game - 18 minutes game length data is loaded.

 >> Processing index : 25413
miniset's size is: (31, 24)
 >> >> Processing index : 1152 game - 31 minutes game length data is loaded.

 >> Processing index : 25414
miniset's size is: (39, 24)
 >> >> Processing index : 5302 game - 39 minutes game length data is loaded.

 >> Processing index : 25415
miniset's size is: (26, 24)
 >> >> Processing index 

miniset's size is: (43, 24)
 >> >> Processing index : 31055 game - 43 minutes game length data is loaded.

 >> Processing index : 25526
miniset's size is: (19, 24)
 >> >> Processing index : 28945 game - 19 minutes game length data is loaded.

 >> Processing index : 25527
miniset's size is: (36, 24)
 >> >> Processing index : 25332 game - 36 minutes game length data is loaded.

 >> Processing index : 25528
miniset's size is: (26, 24)
 >> >> Processing index : 3560 game - 26 minutes game length data is loaded.

 >> Processing index : 25529
miniset's size is: (17, 24)
 >> >> Processing index : 20006 game - 17 minutes game length data is loaded.

 >> Processing index : 25530
miniset's size is: (34, 24)
 >> >> Processing index : 6021 game - 34 minutes game length data is loaded.

 >> Processing index : 25531
miniset's size is: (38, 24)
 >> >> Processing index : 23605 game - 38 minutes game length data is loaded.

 >> Processing index : 25532
miniset's size is: (34, 24)
 >> >> Processing inde

miniset's size is: (17, 24)
 >> >> Processing index : 14935 game - 17 minutes game length data is loaded.

 >> Processing index : 25588
miniset's size is: (32, 24)
 >> >> Processing index : 14116 game - 32 minutes game length data is loaded.

 >> Processing index : 25589
miniset's size is: (13, 24)
 >> >> Processing index : 22258 game - 13 minutes game length data is loaded.

 >> Processing index : 25590
miniset's size is: (5, 24)
 >> >> Processing index : 20757 game - 5 minutes game length data is loaded.

 >> Processing index : 25591
miniset's size is: (31, 24)
 >> >> Processing index : 24275 game - 31 minutes game length data is loaded.

 >> Processing index : 25592
miniset's size is: (21, 24)
 >> >> Processing index : 9225 game - 21 minutes game length data is loaded.

 >> Processing index : 25593
miniset's size is: (22, 24)
 >> >> Processing index : 30403 game - 22 minutes game length data is loaded.

 >> Processing index : 25594
miniset's size is: (32, 24)
 >> >> Processing index

# Make test dataset

In [6]:
dataset = []

print("In test data whole game size is:", len(endTimes_test))

######### initialize ########
dataPath = "./RNN Dataset/{0}/Test/Data/{0}{1}.pkl"
targetPath = "./RNN Dataset/{0}/Test/Target/{0}{1}.pkl"
store_cnt = 1
#############################

for idx in range(len(endTimes_test)):
    miniset = []
    last_timeline = 0
    print("{}th game is loaded.".format(idx))
    game, endTime = endTimes_test[idx]
    
    for tl in range(start, endTime+1):
        last_timeline = tl
        miniset.append(np.array(eval("df_"+str(tl)).iloc[game]))
        
    print("miniset's size is:", np.shape(miniset))
    dataset.append(np.array(miniset))
    print("{0}th game: until {1} minutes game data is loaded.\n".format(game, last_timeline))
    
    if (idx+1) % (10*k) == 0:
        dataset = np.array(dataset)
        
        path = dataPath.format(tier, store_cnt)
        with open(path, "wb") as f: pickle.dump(dataset, f)
            
        path = targetPath.format(tier, store_cnt)
        with open(path, "wb") as f:
            b1, b2 = (store_cnt-1)*10*k, store_cnt*10*k
            pickle.dump(y_test[b1:b2], f)
            
        dataset = []
        store_cnt += 1
        print("Intermediate storing has been done.\n")

dataset = np.array(dataset)
path = dataPath.format(tier, store_cnt)
with open(path, "wb") as f: pickle.dump(dataset, f)
    
path = targetPath.format(tier, store_cnt)
with open(path, "wb") as f:
    b1 = (store_cnt-1)*10*k
    pickle.dump(y_test[b1:], f)
    
print("\n\n\n\nFinished. Final dataset.shape:", dataset.shape)

In test data whole game size is: 6400
0th game is loaded.
miniset's size is: (5, 24)
31330th game: until 5 minutes game data is loaded.

1th game is loaded.
miniset's size is: (18, 24)
3514th game: until 18 minutes game data is loaded.

2th game is loaded.
miniset's size is: (30, 24)
12363th game: until 30 minutes game data is loaded.

3th game is loaded.
miniset's size is: (18, 24)
25927th game: until 18 minutes game data is loaded.

4th game is loaded.
miniset's size is: (25, 24)
31886th game: until 25 minutes game data is loaded.

5th game is loaded.
miniset's size is: (21, 24)
27649th game: until 21 minutes game data is loaded.

6th game is loaded.
miniset's size is: (25, 24)
22894th game: until 25 minutes game data is loaded.

7th game is loaded.
miniset's size is: (17, 24)
15533th game: until 17 minutes game data is loaded.

8th game is loaded.
miniset's size is: (17, 24)
19110th game: until 17 minutes game data is loaded.

9th game is loaded.
miniset's size is: (23, 24)
23606th 

miniset's size is: (21, 24)
30920th game: until 21 minutes game data is loaded.

103th game is loaded.
miniset's size is: (27, 24)
25970th game: until 27 minutes game data is loaded.

104th game is loaded.
miniset's size is: (21, 24)
7453th game: until 21 minutes game data is loaded.

105th game is loaded.
miniset's size is: (15, 24)
12212th game: until 15 minutes game data is loaded.

106th game is loaded.
miniset's size is: (17, 24)
22311th game: until 17 minutes game data is loaded.

107th game is loaded.
miniset's size is: (28, 24)
15193th game: until 28 minutes game data is loaded.

108th game is loaded.
miniset's size is: (23, 24)
16553th game: until 23 minutes game data is loaded.

109th game is loaded.
miniset's size is: (33, 24)
11413th game: until 33 minutes game data is loaded.

110th game is loaded.
miniset's size is: (37, 24)
2508th game: until 37 minutes game data is loaded.

111th game is loaded.
miniset's size is: (24, 24)
1584th game: until 24 minutes game data is load

miniset's size is: (20, 24)
29446th game: until 20 minutes game data is loaded.

196th game is loaded.
miniset's size is: (40, 24)
13904th game: until 40 minutes game data is loaded.

197th game is loaded.
miniset's size is: (22, 24)
30531th game: until 22 minutes game data is loaded.

198th game is loaded.
miniset's size is: (31, 24)
2330th game: until 31 minutes game data is loaded.

199th game is loaded.
miniset's size is: (37, 24)
8586th game: until 37 minutes game data is loaded.

200th game is loaded.
miniset's size is: (24, 24)
2373th game: until 24 minutes game data is loaded.

201th game is loaded.
miniset's size is: (23, 24)
22637th game: until 23 minutes game data is loaded.

202th game is loaded.
miniset's size is: (25, 24)
9233th game: until 25 minutes game data is loaded.

203th game is loaded.
miniset's size is: (23, 24)
28381th game: until 23 minutes game data is loaded.

204th game is loaded.
miniset's size is: (25, 24)
20586th game: until 25 minutes game data is loade

miniset's size is: (29, 24)
16958th game: until 29 minutes game data is loaded.

299th game is loaded.
miniset's size is: (26, 24)
14601th game: until 26 minutes game data is loaded.

300th game is loaded.
miniset's size is: (16, 24)
26803th game: until 16 minutes game data is loaded.

301th game is loaded.
miniset's size is: (31, 24)
31557th game: until 31 minutes game data is loaded.

302th game is loaded.
miniset's size is: (22, 24)
18148th game: until 22 minutes game data is loaded.

303th game is loaded.
miniset's size is: (11, 24)
12971th game: until 11 minutes game data is loaded.

304th game is loaded.
miniset's size is: (32, 24)
16474th game: until 32 minutes game data is loaded.

305th game is loaded.
miniset's size is: (16, 24)
9342th game: until 16 minutes game data is loaded.

306th game is loaded.
miniset's size is: (19, 24)
8771th game: until 19 minutes game data is loaded.

307th game is loaded.
miniset's size is: (21, 24)
29673th game: until 21 minutes game data is loa

miniset's size is: (18, 24)
10190th game: until 18 minutes game data is loaded.

391th game is loaded.
miniset's size is: (24, 24)
26684th game: until 24 minutes game data is loaded.

392th game is loaded.
miniset's size is: (26, 24)
1237th game: until 26 minutes game data is loaded.

393th game is loaded.
miniset's size is: (19, 24)
17199th game: until 19 minutes game data is loaded.

394th game is loaded.
miniset's size is: (26, 24)
8953th game: until 26 minutes game data is loaded.

395th game is loaded.
miniset's size is: (22, 24)
8325th game: until 22 minutes game data is loaded.

396th game is loaded.
miniset's size is: (23, 24)
12924th game: until 23 minutes game data is loaded.

397th game is loaded.
miniset's size is: (22, 24)
30389th game: until 22 minutes game data is loaded.

398th game is loaded.
miniset's size is: (23, 24)
30772th game: until 23 minutes game data is loaded.

399th game is loaded.
miniset's size is: (18, 24)
7544th game: until 18 minutes game data is loade

...

miniset's size is: (17, 24)
29298th game: until 17 minutes game data is loaded.

5987th game is loaded.
miniset's size is: (17, 24)
13019th game: until 17 minutes game data is loaded.

5988th game is loaded.
miniset's size is: (25, 24)
8859th game: until 25 minutes game data is loaded.

5989th game is loaded.
miniset's size is: (34, 24)
24988th game: until 34 minutes game data is loaded.

5990th game is loaded.
miniset's size is: (17, 24)
29616th game: until 17 minutes game data is loaded.

5991th game is loaded.
miniset's size is: (17, 24)
1760th game: until 17 minutes game data is loaded.

5992th game is loaded.
miniset's size is: (16, 24)
23595th game: until 16 minutes game data is loaded.

5993th game is loaded.
miniset's size is: (27, 24)
3033th game: until 27 minutes game data is loaded.

5994th game is loaded.
miniset's size is: (16, 24)
25286th game: until 16 minutes game data is loaded.

5995th game is loaded.
miniset's size is: (27, 24)
20224th game: until 27 minutes game dat

17651th game: until 25 minutes game data is loaded.

6085th game is loaded.
miniset's size is: (26, 24)
6745th game: until 26 minutes game data is loaded.

6086th game is loaded.
miniset's size is: (35, 24)
8147th game: until 35 minutes game data is loaded.

6087th game is loaded.
miniset's size is: (14, 24)
13539th game: until 14 minutes game data is loaded.

6088th game is loaded.
miniset's size is: (22, 24)
21236th game: until 22 minutes game data is loaded.

6089th game is loaded.
miniset's size is: (22, 24)
17079th game: until 22 minutes game data is loaded.

6090th game is loaded.
miniset's size is: (29, 24)
1165th game: until 29 minutes game data is loaded.

6091th game is loaded.
miniset's size is: (23, 24)
7230th game: until 23 minutes game data is loaded.

6092th game is loaded.
miniset's size is: (21, 24)
8065th game: until 21 minutes game data is loaded.

6093th game is loaded.
miniset's size is: (17, 24)
16623th game: until 17 minutes game data is loaded.

6094th game is l

miniset's size is: (32, 24)
30803th game: until 32 minutes game data is loaded.

6175th game is loaded.
miniset's size is: (23, 24)
19662th game: until 23 minutes game data is loaded.

6176th game is loaded.
miniset's size is: (15, 24)
22988th game: until 15 minutes game data is loaded.

6177th game is loaded.
miniset's size is: (28, 24)
10164th game: until 28 minutes game data is loaded.

6178th game is loaded.
miniset's size is: (25, 24)
16310th game: until 25 minutes game data is loaded.

6179th game is loaded.
miniset's size is: (17, 24)
24657th game: until 17 minutes game data is loaded.

6180th game is loaded.
miniset's size is: (31, 24)
23144th game: until 31 minutes game data is loaded.

6181th game is loaded.
miniset's size is: (17, 24)
5357th game: until 17 minutes game data is loaded.

6182th game is loaded.
miniset's size is: (15, 24)
20260th game: until 15 minutes game data is loaded.

6183th game is loaded.
miniset's size is: (32, 24)
8249th game: until 32 minutes game da

miniset's size is: (40, 24)
22239th game: until 40 minutes game data is loaded.

6274th game is loaded.
miniset's size is: (17, 24)
22429th game: until 17 minutes game data is loaded.

6275th game is loaded.
miniset's size is: (27, 24)
470th game: until 27 minutes game data is loaded.

6276th game is loaded.
miniset's size is: (23, 24)
24155th game: until 23 minutes game data is loaded.

6277th game is loaded.
miniset's size is: (31, 24)
6978th game: until 31 minutes game data is loaded.

6278th game is loaded.
miniset's size is: (32, 24)
20048th game: until 32 minutes game data is loaded.

6279th game is loaded.
miniset's size is: (25, 24)
5868th game: until 25 minutes game data is loaded.

6280th game is loaded.
miniset's size is: (24, 24)
17366th game: until 24 minutes game data is loaded.

6281th game is loaded.
miniset's size is: (38, 24)
1034th game: until 38 minutes game data is loaded.

6282th game is loaded.
miniset's size is: (35, 24)
24274th game: until 35 minutes game data 

miniset's size is: (22, 24)
20266th game: until 22 minutes game data is loaded.

6362th game is loaded.
miniset's size is: (18, 24)
14001th game: until 18 minutes game data is loaded.

6363th game is loaded.
miniset's size is: (28, 24)
23186th game: until 28 minutes game data is loaded.

6364th game is loaded.
miniset's size is: (23, 24)
14237th game: until 23 minutes game data is loaded.

6365th game is loaded.
miniset's size is: (23, 24)
5108th game: until 23 minutes game data is loaded.

6366th game is loaded.
miniset's size is: (19, 24)
4643th game: until 19 minutes game data is loaded.

6367th game is loaded.
miniset's size is: (24, 24)
25214th game: until 24 minutes game data is loaded.

6368th game is loaded.
miniset's size is: (18, 24)
28263th game: until 18 minutes game data is loaded.

6369th game is loaded.
miniset's size is: (17, 24)
21578th game: until 17 minutes game data is loaded.

6370th game is loaded.
miniset's size is: (29, 24)
533th game: until 29 minutes game data